# import

In [3]:
import sys
import gensim
import string
import nltk
import copy
import json
import numpy as np
import matplotlib.pyplot as plt
import requests as req
import pyLDAvis
import pyLDAvis.gensim
from time import sleep
from collections import Counter
from sklearn import datasets
from wordcloud import WordCloud
from nltk.corpus import stopwords
from bs4 import BeautifulSoup
from janome.tokenizer import Tokenizer
%matplotlib inline

# stopwords

In [296]:
stopwords_ja = ["し", "い", "よう", "こと", "いる", "あり", "ある", "これ", "さ", "する", "れ",
             "て", "くれる", "やっ", "でき", "ため", "も", "なり"]

## 形態素解析

In [4]:
def janome(text, flag):
    tokenizer = Tokenizer()
    #nltk.download('stopwords')
    stopwords_en = stopwords.words('english')
    sentenses = text
    page = []
    for sentence in sentenses:
        tmp = []
        for token in tokenizer.tokenize(sentence):
            pos = token.part_of_speech.split(',')[0]
            if pos in ["名詞", "動詞", "形容詞"]:   # 対象とする品詞
                #print(str(token.surface))
                if not str(token.surface).lower() in stopwords_ja:
                    tmp.append(str(token.surface).lower())
        page.append(tmp)
    page_copy = copy.deepcopy(page)

    for i in range(len(page_copy)):
        for j in range(len(page_copy[i])):
            if page_copy[i][j] == " ":
                page[i].remove(" ")
            elif page_copy[i][j] in stopwords_en:
                page[i].remove(page_copy[i][j])
    if flag == True:
        return page
    clean_symbol(page, flag)

## delete symbol

In [5]:
def clean_symbol(page, flag):
    pages = []
    for line in page:
        tmp = []
        for w in line:
            symbol = w.translate(str.maketrans( '', '',string.punctuation))
            if symbol != '':
                tmp.append(symbol)
        pages.append(tmp)
    clean_space(pages, flag)

## delete space

In [6]:
def clean_space(pages,flag):
    for p in pages:
        if p == []:
            pages.remove([])
    topic_model(pages)

# web text

In [41]:
def get_text(url):
    #url = 'https://atcoder.jp/contests/abc084/tasks/abc084_d'
    try:
        html = req.get(url).content
        soup = BeautifulSoup(html, 'html.parser')
        texts = soup.find_all('p')
        text = []
        for p in texts:
            text.append(p.get_text())
        janome(text)
    except:
        print(url, "NO")

# topic model

In [325]:
def topic_model(pages):
    global di
    global check
    global test2
    dic = gensim.corpora.Dictionary(pages)
    corpus = [dic.doc2bow(p) for p in pages]
    num_topics = 50

    lda = gensim.models.ldamodel.LdaModel(
        corpus=corpus,
        num_topics=num_topics,
        id2word=dic,
        random_state = 1)
    
    #get_topic_number(test2, lda, 10)
    json_open = open('C:/Users/bi17030/Documents/researchub/create-chunk/history/historyk.json',mode='r', encoding='utf8')
    json_load = json.load(json_open)
    for i in range(len(json_load)):
        di = json_load[i]['id']
        web_text = get_text_new(json_load[i]['url'],[])
        print(json_load[i]["id"], json_load[i]["url"])
        if web_text != False:
            get_topic_number(web_text, lda, di)
        sleep(1)
    sys.exit()
    visualize(lda, corpus, dic, num_topics)
    """
    topic = []
    per = []
    for i in range(5):
        result = lda.show_topic(i, 5)
        print(result)
        topic.append(result[0][0])
        per.append(str(result[0][1]))
    adr_dict = dict(zip(topic, per))
    adr_dict['id'] = di
    print(adr_dict)
    result = json.dumps(adr_dict, indent=4)
    print(result)
    with open('test.json', mode='a', encoding='utf-8') as f:
        f.write(","+result)
    """

In [322]:
def get_topic_number(corpus, lda, di):
    text = janome(corpus, True)
    dic = gensim.corpora.Dictionary(text)
    corpus = [dic.doc2bow(p) for p in text]
    topics = lda.get_document_topics(corpus, per_word_topics=False)
    save_topic(topics, di)
    #sys.exit()

## save topic

In [347]:
temp = []
def save_topic(topic, di):
    global temp
    topic_num = [[0, i+1] for i in range(50)]
    topic_ls = []
    try:
        for t in topic:
            topic_ls.append(t)
            print(t)
        return
    except:
        temp.append(1)
        return
    """
    for i in range(len(topic_ls)):
        topic_num[topic_ls[i][0]][0] += topic_ls[i][1]            
    """
    for i in range(len(topic_ls)):
        for j in range(len(topic_ls[i])):
            print(topic_num[topic_ls[0][0]][0], topic_ls[0][0])
            topic_num[topic_ls[i][j]][0] += topic_ls[i][j]
    
    topic_num_sort = sorted(topic_num, reverse=True)
    
    #with open('topic.txt', mode='a', encoding='utf8') as f:
    #    f.write("id"+di+str(topic_num_sort[:6]))

In [345]:
temp[28]

IndexError: index 666 is out of bounds for axis 1 with size 632

In [184]:
def get_json():
    global di
    json_open = open('C:/Users/bi17030/Documents/researchub/create-chunk/history/historyk.json',mode='r', encoding='utf8')
    json_load = json.load(json_open)
    for i in range(len(json_load)):
        di = json_load[i]['id']
        print_text(json_load[i]['url'])
        print(json_load[i]["id"],json_load[i]["url"])
        sleep(1)

## visualize

In [10]:
def visualize(lda, corpus, dic, num_topics):
    pyLDAvis.enable_notebook()
    vis = pyLDAvis.gensim.prepare(lda, corpus, dic, sort_topics=False)
    pyLDAvis.save_html(vis, 'pyldavis_output{}.html'.format(num_topics))

In [40]:
get_text("https://qiita.com/fujino-fpu/items/d92d185da730e25743cb")

[('メニュー', 0.02756385), ('doratex', 0.015910653), ('設定', 0.015899826), ('プロジェクト', 0.015265357), ('以下', 0.015064072)]
[('プロジェクト', 0.045937564), ('日本語', 0.030412784), ('作成', 0.02929176), ('よい', 0.021104619), ('ファイル', 0.01916929)]
[('日本語', 0.031868737), ('作成', 0.026835805), ('tex', 0.025924616), ('サービス', 0.022494249), ('論文', 0.017824218)]
[('コンパイル', 0.029517353), ('ペイン', 0.02028515), ('右側', 0.02028153), ('tex', 0.018121235), ('セル', 0.01564397)]
[('ファイル', 0.04451961), ('以下', 0.028052224), ('もの', 0.024327781), ('中身', 0.019303195), ('際', 0.015596169)]


In [350]:
len(temp)

17

In [348]:
janome(all_lines[0:100], False)

1056 https://github.com/kisikisikisi
[(32, 0.67000294), (36, 0.16999438)]
[(11, 0.25499266), (36, 0.50500304)]
[(6, 0.16998968), (11, 0.33667377), (32, 0.1699959), (36, 0.16999987)]
[(6, 0.25499535), (9, 0.25498748), (36, 0.25500512)]
[(9, 0.89000976), (32, 0.056655265)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (1

1342 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=Unit%205.pdf
1338 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A
1340 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=2019ACT-R_Unit4_nishikawa_slide.pdf
974 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?%E5%8B%89%E5%BC%B7%E4%BC%9A
401 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?%E3%83%9F%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%E8%A8%98%E9%8C%B2
836 https://qiita.com/fujino-fpu/items/d92d185da730e25743cb
[(6, 0.10299303), (9, 0.54607177), (11, 0.104129136), (32, 0.13950342), (36, 0.08002851)]
[(0, 0.335557), (9, 0.1133109), (29, 0.44668287)]
[(9, 0.23230217), (26, 0.07846103), (29, 0.07845965), (30, 0.3861703), (32, 0.07845321), (36, 0.07845737)]
[(9, 0.13706844), (13, 0.30408153), (32, 0.15813886), (36, 0.16048443), (40, 0.12771976)]
[(9, 0.0

1332 https://www.google.com/search?sxsrf=ALeKk00gIiQz0YKasa6l1YfM7rpXW_Ta3Q%3A1591159531032&ei=6yrXXsDHAcim0wT7woGQCA&q=Package+inputenc+Error%3A+Unicode+character++%5E%5E83+%28U%2B0083%29+overleaf&oq=Package+inputenc+Error%3A+Unicode+character++%5E%5E83+%28U%2B0083%29+overleaf&gs_lcp=CgZwc3ktYWIQA1D2QViFWGCOWWgAcAB4AIABkAGIAYwHkgEDOS4xmAEAoAEBqgEHZ3dzLXdpeg&sclient=psy-ab&ved=0ahUKEwiA6YKV6-TpAhVI05QKHXthAIIQ4dUDCAw&uact=5
[(32, 0.67333055)]
[(32, 0.67333055)]
[(6, 0.2613115), (11, 0.27972585), (32, 0.18488905), (36, 0.20330197)]
[(9, 0.5577807), (32, 0.11332479), (36, 0.22444618)]
[(9, 0.7512598), (32, 0.12624471), (36, 0.0637434)]
[(9, 0.28856152), (32, 0.28857246), (36, 0.28857547)]
[(9, 0.6381873), (32, 0.18363328), (36, 0.09272183)]
[(0, 0.27454108), (11, 0.092717566), (26, 0.18363896), (29, 0.3654631)]
[(9, 0.2858782), (26, 0.21745628), (29, 0.08499709), (30, 0.25167048), (36, 0.0849948)]
[(9, 0.547279), (11, 0.09271838), (29, 0.09272482), (36, 0.1836378)]
[(9, 0.78000295), (36,

1328 https://www.google.com/search?sxsrf=ALeKk00OZjHV7UOQyBQWHCAO2IvRRDtq1g%3A1591158864516&ei=UCjXXr-BH5XemAWZpYTgCg&q=latex+error+this+file+needs+format+platex2e%27+overleaf&oq=LaTeX+Error%3A+This+file+needs+format+%60pLaTeX2e%27&gs_lcp=CgZwc3ktYWIQARgBMgIIADICCABQAFgAYNInaABwAHgAgAFniAFnkgEDMC4xmAEAqgEHZ3dzLXdpeg&sclient=psy-ab
[(32, 0.67333055)]
[(32, 0.67333055)]
[(6, 0.09994414), (11, 0.34829807), (32, 0.10988432), (36, 0.3582337)]
[(6, 0.27326542), (9, 0.44666472), (36, 0.17562157)]
[(9, 0.7291021), (11, 0.09271794), (36, 0.092722125)]
[(9, 0.6040067), (11, 0.11170879), (32, 0.09627685)]
[(9, 0.40399644), (32, 0.20399605), (36, 0.20399994)]
[(11, 0.20399253), (26, 0.2039999), (36, 0.4040032)]
[(0, 0.30200258), (9, 0.10197782), (29, 0.4020177), (36, 0.10199685)]
[(9, 0.11331336), (26, 0.1133359), (29, 0.113334544), (30, 0.33557138), (32, 0.11332821), (36, 0.113332294)]
[(9, 0.14569432), (29, 0.14571516), (32, 0.28857622), (36, 0.28857926)]
[(0, 0.010000136), (1, 0.010000136), (2,

[(9, 0.75499564)]
[(0, 0.010000271), (1, 0.010000271), (2, 0.010000271), (3, 0.010000271), (4, 0.010000271), (5, 0.010000271), (6, 0.010000271), (7, 0.010000271), (8, 0.010000271), (9, 0.010000271), (10, 0.010000271), (11, 0.010000271), (12, 0.010000271), (13, 0.010000271), (14, 0.010000271), (15, 0.010000271), (16, 0.010000271), (17, 0.010000271), (18, 0.010000271), (19, 0.010000271), (20, 0.010000271), (21, 0.010000271), (22, 0.010000271), (23, 0.010000271), (24, 0.010000271), (25, 0.010000271), (26, 0.010000271), (27, 0.5099867), (28, 0.010000271), (29, 0.010000271), (30, 0.010000271), (31, 0.010000271), (32, 0.010000271), (33, 0.010000271), (34, 0.010000271), (35, 0.010000271), (36, 0.010000271), (37, 0.010000271), (38, 0.010000271), (39, 0.010000271), (40, 0.010000271), (41, 0.010000271), (42, 0.010000271), (43, 0.010000271), (44, 0.010000271), (45, 0.010000271), (46, 0.010000271), (47, 0.010000271), (48, 0.010000271), (49, 0.010000271)]
[(27, 0.76763695)]
[(0, 0.010000271), (1, 0

...

12 https://support.microsoft.com/ja-jp/help/4028379/windows-10-how-to-use-remote-desktop
[(32, 0.67000294), (36, 0.1699944)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(32, 0.50333226), (36, 0.33666536)]
[(6, 0.28856632), (11, 0.43143344), (36, 0.14571033)]
[(6, 0.20199198), (9, 0.70200497)]
[(9, 0.5049965), (32, 0.2549961)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (

5 https://www.google.com/search?ei=42N4XoHfI8fN-QatxIqABw&q=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97+windows10&oq=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&gs_l=psy-ab.1.4.0l8.3204.5399..8298...0.2..0.76.832.12......0....1..gws-wiz.......0i71j0i4.N1EquyAra0U
[(32, 0.67333055)]
[(32, 0.67333055)]
[(6, 0.17581345), (9, 0.15537257), (11, 0.29480192), (32, 0.092894465), (36, 0.21188277)]
[(9, 0.5025001), (11, 0.2524996), (36, 0.12749602)]
[(9, 0.30199403), (11, 0.27488372), (32, 0.12911597), (36, 0.20200226)]
[(9, 0.36545187), (11, 0.24959767), (32, 0.117672876), (36, 0.18363765)]
[(9, 0.30199403), (11, 0.2741054), (32, 0.12989439), (36, 0.20200221)]
[(9, 0.38615212), (11, 0.21144316), (32, 0.09932108), (36, 0.23231143)]
[(9, 0.30199403), (11, 0.27440378), (32, 0.12959595), (36, 0.20200224)]
[(9, 0.30199403), (11, 0.27429718), (32, 0.12970257), (36, 0.20200221)]
[(6, 0.153681), (11, 0.3426821

2 https://www.google.com/search?ei=2GF4Xsr8K4H8wQPEhrXYBQ&q=windows+%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&oq=windows+rimo&gs_l=psy-ab.3.0.0i4l8.6864.35396..37748...9.0..0.103.3129.38j2......0....1..gws-wiz.....6..0i7i10i30j0j0i10i30j0i30j0i131i4j0i131j0i362i308i154i357j0i13j0i4i30j0i4i10i30j0i8i7i30j0i8i30j0i13i4i30j0i13i10i30j0i8i13i4i30j0i8i13i10i30j0i13i5i30j0i7i4i30j0i13i10j0i13i30j0i5i30j0i8i4i30.jBDHn7CYt2o
[(32, 0.67333055)]
[(32, 0.67333055)]
[(6, 0.17574967), (9, 0.15537257), (11, 0.2947353), (32, 0.09296112), (36, 0.21194653)]
[(9, 0.5025002), (11, 0.25249958), (36, 0.127496)]
[(9, 0.3654519), (11, 0.24979931), (32, 0.11747121), (36, 0.18363766)]
[(9, 0.38615212), (11, 0.2115266), (32, 0.099237606), (36, 0.23231144)]
[(9, 0.46308073), (11, 0.15538207), (32, 0.07845222), (36, 0.23231243)]
[(9, 0.3019941), (11, 0.27462497), (32, 0.12937474), (36, 0.20200223)]
[(9, 0.36545187), (11, 0.24983431), (32, 0.11743621), (36, 0.183637

SystemExit: 

C:\Users\bi17030\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2971: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [259]:
json_open = open('history/historyk.json',mode='r', encoding='utf8')
json_load = json.load(json_open)
for i in range(len(json_load)):
    di = json_load[i]['id']
    get_text(json_load[i]['url'])
    print(json_load[i]["id"],json_load[i]["url"])
    sleep(5)

[('notebook', 0.14334644), ('jupyter', 0.14259897), ('knowledge', 0.078345805), ('declarative', 0.07796918), ('javascript', 0.014047343)]
[('learn', 0.09737253), ('abuse', 0.09717318), ('reporting', 0.09714411), ('javascript', 0.017385684), ('newlisp', 0.016993362)]
[('javascript', 0.11805516), ('user', 0.065844126), ('contact', 0.06576868), ('support', 0.06571011), ('navigation', 0.06564838)]
[('html', 0.09648299), ('newlisp', 0.096057996), ('algorithm', 0.09600423), ('javascript', 0.01751577), ('jupyter', 0.017048858)]
[('github', 0.053379968), ('profile', 0.05335891), ('developers', 0.02913229), ('best', 0.029131208), ('manage', 0.02912933)]
{'html': '0.09648299', 'id': '1056', 'javascript': '0.11805516', 'learn': '0.09737253', 'notebook': '0.14334644', 'github': '0.053379968'}
{
    "html": "0.09648299",
    "id": "1056",
    "javascript": "0.11805516",
    "learn": "0.09737253",
    "notebook": "0.14334644",
    "github": "0.053379968"
}
1056 https://github.com/kisikisikisi
https:

https://www.google.com/search?sxsrf=ALeKk00OZjHV7UOQyBQWHCAO2IvRRDtq1g%3A1591158864516&ei=UCjXXr-BH5XemAWZpYTgCg&q=latex+error+this+file+needs+format+platex2e%27+overleaf&oq=LaTeX+Error%3A+This+file+needs+format+%60pLaTeX2e%27&gs_lcp=CgZwc3ktYWIQARgBMgIIADICCABQAFgAYNInaABwAHgAgAFniAFnkgEDMC4xmAEAqgEHZ3dzLXdpeg&sclient=psy-ab NO
1328 https://www.google.com/search?sxsrf=ALeKk00OZjHV7UOQyBQWHCAO2IvRRDtq1g%3A1591158864516&ei=UCjXXr-BH5XemAWZpYTgCg&q=latex+error+this+file+needs+format+platex2e%27+overleaf&oq=LaTeX+Error%3A+This+file+needs+format+%60pLaTeX2e%27&gs_lcp=CgZwc3ktYWIQARgBMgIIADICCABQAFgAYNInaABwAHgAgAFniAFnkgEDMC4xmAEAqgEHZ3dzLXdpeg&sclient=psy-ab
[('回答', 0.038822625), ('表示', 0.03863659), ('解決', 0.03361497), ('済', 0.03221007), ('評価', 0.026325392)]
[('回答', 0.07974641), ('評価', 0.06007112), ('0', 0.033940822), ('クリップ', 0.02750912), ('上げ', 0.027403997)]
[('更新', 0.039929558), ('解決', 0.027099572), ('済', 0.026903963), ('回答', 0.020859204), ('評価', 0.02085904)]
[('回答', 0.04201237), ('クリッ

[('系', 0.024226593), ('思い', 0.02133982), ('platex', 0.01873673), ('出', 0.01667596), ('の', 0.014439513)]
[('latex', 0.030584846), ('platex', 0.02612371), ('もの', 0.024280982), ('policy', 0.022286262), ('サイト', 0.021549368)]
[('rss', 0.031366587), ('ください', 0.019877123), ('tex', 0.017881703), ('リーダー', 0.01712675), ('購読', 0.017126162)]
[('設定', 0.041999627), ('思い', 0.02778167), ('の', 0.024486732), ('環境', 0.022385681), ('tex', 0.02203053)]
[('サイト', 0.035056986), ('2020', 0.022863438), ('公開', 0.022636192), ('必須', 0.022633513), ('フロー', 0.022503966)]
{'rss': '0.031366587', '系': '0.024226593', 'サイト': '0.035056986', '設定': '0.041999627', 'id': '1321', 'latex': '0.030584846'}
{
    "rss": "0.031366587",
    "\u7cfb": "0.024226593",
    "\u30b5\u30a4\u30c8": "0.035056986",
    "\u8a2d\u5b9a": "0.041999627",
    "id": "1321",
    "latex": "0.030584846"
}
1321 https://ja.stackoverflow.com/questions/31298/latex%E3%81%AE%E3%82%B3%E3%83%B3%E3%83%91%E3%82%A4%E3%83%AB%E6%99%82%E3%81%ABthis-file-needs-format-

https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=%E3%83%9F%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%E8%A8%98%E9%8C%B2&openfile=20200601_InoueNaoki.pdf NO
1313 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=%E3%83%9F%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%E8%A8%98%E9%8C%B2&openfile=20200601_InoueNaoki.pdf
https://www.google.com/search?q=Javascript+%E3%82%A4%E3%83%B3%E3%83%87%E3%83%83%E3%82%AF%E3%82%B9+%E6%9C%80%E5%BE%8C%E5%88%97&oq=Javascript+%E3%82%A4%E3%83%B3%E3%83%87%E3%83%83%E3%82%AF%E3%82%B9%E3%80%80%E6%9C%80%E5%BE%8C%E5%88%97&aqs=chrome..69i57.17625j0j4&sourceid=chrome&ie=UTF-8 NO
1306 https://www.google.com/search?q=Javascript+%E3%82%A4%E3%83%B3%E3%83%87%E3%83%83%E3%82%AF%E3%82%B9+%E6%9C%80%E5%BE%8C%E5%88%97&oq=Javascript+%E3%82%A4%E3%83%B3%E3%83%87%E3%83%83%E3%82%AF%E3%82%B9%E3%80%80%E6%9C%80%E5%BE%8C%E5%88%97&aqs=chrome..69i57.17625j0j4&sourceid=chrome&ie=UTF-8
[('メソッド', 0.04124589), ('直接', 0.04123422), ('追加', 0.041218

https://www.google.com/search?q=Javascript+break&oq=Javascript+break&aqs=chrome..69i57j0l7.4840j0j4&sourceid=chrome&ie=UTF-8 NO
1291 https://www.google.com/search?q=Javascript+break&oq=Javascript+break&aqs=chrome..69i57j0l7.4840j0j4&sourceid=chrome&ie=UTF-8
[('delivered', 0.039044607), ('mdn', 0.03903719), ('inbox', 0.039020684), ('get', 0.039016634), ('latest', 0.039008263)]
[('作成', 0.07061548), ('ログイン', 0.070297316), ('アカウント', 0.06997532), ('mdn', 0.0384631), ('特典', 0.03844977)]
[('interactive', 0.06128418), ('examples', 0.04213499), ('github', 0.042128477), ('文', 0.026932929), ('mdn', 0.0235393)]
[('文', 0.07801409), ('break', 0.06844849), ('ラベル', 0.045167178), ('block', 0.039521556), ('次', 0.034828614)]
[('文', 0.18459636), ('ラベル', 0.08246515), ('break', 0.0518161), ('付き', 0.050692637), ('中断', 0.038876135)]
{'delivered': '0.039044607', 'id': '1292', '文': '0.18459636', 'interactive': '0.06128418', '作成': '0.07061548'}
{
    "delivered": "0.039044607",
    "id": "1292",
    "\u6587": "0

...

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


https://sourceforge.net/projects/sbcl/files/sbcl/1.2.7/sbcl-1.2.7-x86-64-windows-binary.msi/download NO
46 https://sourceforge.net/projects/sbcl/files/sbcl/1.2.7/sbcl-1.2.7-x86-64-windows-binary.msi/download
[('トンネル', 0.037007343), ('データ', 0.03653229), ('でき', 0.03544814), ('守る', 0.031860277), ('中', 0.029336011)]
[('field', 0.014600746), ('seem', 0.0145656895), ('css', 0.014539262), ('please', 0.01453045), ('fill', 0.014500662)]
[('please', 0.08310097), ('seem', 0.05722257), ('turned', 0.057148416), ('fill', 0.057114024), ('field', 0.057097822)]
[('中', 0.037696965), ('守る', 0.033486046), ('データ', 0.031152537), ('トンネル', 0.030984469), ('でき', 0.030912038)]
[('please', 0.056066293), ('turned', 0.03856163), ('fill', 0.03855707), ('css', 0.038553715), ('field', 0.03847018)]
{'トンネル': '0.037007343', '中': '0.037696965', 'id': '45', 'please': '0.056066293', 'field': '0.014600746'}
{
    "\u30c8\u30f3\u30cd\u30eb": "0.037007343",
    "\u4e2d": "0.037696965",
    "id": "45",
    "please": "0.05606629

[('おり', 0.022990339), ('良い', 0.01168443), ('端末', 0.011630343), ('3', 0.010823781), ('できる', 0.010305156)]
[('pc', 0.014467707), ('操作', 0.013485781), ('年', 0.013431471), ('teamviewer', 0.01302431), ('ボタン', 0.009814628)]
[('操作', 0.014753457), ('teamviewer', 0.014496299), ('初心者', 0.013507917), ('私', 0.013408531), ('できる', 0.012815601)]
[('teamviewer', 0.026880687), ('コス', 0.023470657), ('パ', 0.02346456), ('安定', 0.018292392), ('インストール', 0.015432761)]
[('操作', 0.021903858), ('teamviewer', 0.021029143), ('パソコン', 0.012498937), ('押し', 0.01045976), ('ボタン', 0.009991341)]
{'おり': '0.022990339', 'id': '31', '操作': '0.021903858', 'pc': '0.014467707', 'teamviewer': '0.026880687'}
{
    "\u304a\u308a": "0.022990339",
    "id": "31",
    "\u64cd\u4f5c": "0.021903858",
    "pc": "0.014467707",
    "teamviewer": "0.026880687"
}
31 https://btopc.jp/etc/teamviewer-2018.html
https://www.google.com/search?q=teamviewer+%E4%BD%BF%E3%81%84%E6%96%B9&oq=teamviewe&aqs=chrome.2.0j69i57j0l3j69i60l3.13520j0j4&sourceid=ch

https://www.google.com/search?ei=cGV4XqjOJcT_wAP9xKL4Dg&q=windows+%E4%BD%95%E3%83%93%E3%83%83%E3%83%88&oq=windows+NANN&gs_l=psy-ab.3.0.0i4l8.3176.5152..7016...1.2..0.87.440.6......0....1..gws-wiz.......0i71j0i67j0j0i8i4i30.Gs325SZIIr8 NO
19 https://www.google.com/search?ei=cGV4XqjOJcT_wAP9xKL4Dg&q=windows+%E4%BD%95%E3%83%93%E3%83%83%E3%83%88&oq=windows+NANN&gs_l=psy-ab.3.0.0i4l8.3176.5152..7016...1.2..0.87.440.6......0....1..gws-wiz.......0i71j0i67j0j0i8i4i30.Gs325SZIIr8
https://www.google.com/search?q=windows+%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&oq=W&aqs=chrome.0.69i59j69i57j0l3j69i60l3.12992j0j7&sourceid=chrome&ie=UTF-8 NO
18 https://www.google.com/search?q=windows+%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&oq=W&aqs=chrome.0.69i59j69i57j0l3j69i60l3.12992j0j7&sourceid=chrome&ie=UTF-8
[('月', 0.04635449), ('17', 0.03990535), ('8', 0.039890993), ('日', 0.039875016), ('1', 0.014174723)]
[(

https://www.google.com/search?ei=42N4XoHfI8fN-QatxIqABw&q=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97+windows10&oq=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&gs_l=psy-ab.1.4.0l8.3204.5399..8298...0.2..0.76.832.12......0....1..gws-wiz.......0i71j0i4.N1EquyAra0U NO
5 https://www.google.com/search?ei=42N4XoHfI8fN-QatxIqABw&q=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97+windows10&oq=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88%E3%83%87%E3%82%B9%E3%82%AF%E3%83%88%E3%83%83%E3%83%97&gs_l=psy-ab.1.4.0l8.3204.5399..8298...0.2..0.76.832.12......0....1..gws-wiz.......0i71j0i4.N1EquyAra0U
https://www.google.com/search?q=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88&oq=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88&aqs=chrome..69i57j0l6j69i61.9833j0j7&sourceid=chrome&ie=UTF-8 NO
4 https://www.google.com/search?q=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%88&oq=%E3%83%AA%E3%83%A2%E3%83%BC%E3%83%8

## get text new

In [323]:
def get_text_new(url, text):
    #global text
    try:
        html = req.get(url).content
        soup = BeautifulSoup(html, 'html.parser')
        append_text('p', soup, text)
        append_text('h1', soup, text)
        append_text('h2', soup, text)
        append_text('h3', soup, text)
        return text
        #print(text)
    except:
        return False
    
def check_tag(tag,soup):
    try:
        texts = soup.find_all(tag)
        return texts
    except:
        return
    
def append_text(tag, soup, text):
    texts = check_tag(tag, soup)
    for p in texts:
        text.append(p.get_text())

In [295]:
get_text_new("https://qiita.com/fujino-fpu/items/d92d185da730e25743cb", [])

['Overleafはウェブブラウザ上でtex文書を作成できるクラウドサービス．\ntexは環境構築が結構面倒なので（昔に比べりゃ楽になったが，時間がかかるのは変わらない），このサービスは非常にありがたい．\nただ，日本語論文を作成するにはちょっとひと手間必要になる．\n以下，備忘録として日本語論文作成方法をメモする．',
 '以下のページを参考：\nhttp://doratex.hatenablog.jp/entry/20180503/1525338512',
 'まあ，まずはプロジェクトを作らないことには始まらないので，プロジェクトを作成．\nOverleafそのものは日本語化されているので，これは簡単にできるはず．\n\nまあ，まずは空のプロジェクト作成でよいと思う．',
 '作ると勝手にtexファイルも作ってくれる．\n試しに日本語を打ち込んでみるが，エラーになって反映されてない．\n',
 'ちなみにコンパイルはCtrl+sでやってくれて，右側ペインに印刷イメージが表示される．\nまた右側ペインの上の「再編集」というボタンのプルダウンメニューでAuto Compileをオンにすると，手動でコンパイルしなくても都度勝手にコンパイルしてくれる．',
 '左上の「メニュー」をクリックすると，プロジェクトの設定を触るメニューが現れる．\nこの中のコンパイラが標準では「pdfLatex」になっているが，これを「Latex」にする．',
 '次にプロジェクトに新しいファイルとしてlatexmkrcというファイルを作る．\n中身は以下の通り．',
 'この中身が意味しているものはよー分からんでも，とにかく上記のとおりに打つ．',
 'これを作ったら，あとはソースファイルをコンパイルすれば日本語が表示される．\n',
 '学会等で提供されているクラスファイルやフォーマットを使うことは多いだろう．\nそれらをOverleafのプロジェクトにそのままアップロードして，うまく使えればよいが，中には古いウィンドウズのTex環境下で作られていてうまく動かないこともある．\nそんな場合には，次の点をチェックしてみるとよい．',
 'ソースファイルの冒頭でクラスファイルを設定する際に，古いものだと以下のように記述していることがある．',
 'この[dviout]を[dvipdfmx]に

In [7]:
json_open = open('C:/Users/bi17030/Documents/researchub/create-chunk/history/historyk.json',mode='r', encoding='utf8')
json_load = json.load(json_open)
text = []
for i in range(len(json_load)):
    di = json_load[i]['id']
    print_text(json_load[i]['url'])
    print(json_load[i]["id"],json_load[i]["url"])
    sleep(1)

1056 https://github.com/kisikisikisi
https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=Unit%205.pdf NO
1342 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=Unit%205.pdf
https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A NO
1338 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A
https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=2019ACT-R_Unit4_nishikawa_slide.pdf NO
1340 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?plugin=attach&refer=ACT-R%E5%8B%89%E5%BC%B7%E4%BC%9A&openfile=2019ACT-R_Unit4_nishikawa_slide.pdf
https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?%E5%8B%89%E5%BC%B7%E4%BC%9A NO
974 https://moritalab.inf.shizuoka.ac.jp/sites/pukiwiki/?%E5%8B%89%E5%BC%B7%E4%BC%9A
https://moritalab.inf.shizuoka.ac.jp/sit

1298 https://qiita.com/n_oshiumi/items/5795de01187d5aafca07
1297 https://www.google.com/search?q=javascript+%E8%A6%81%E7%B4%A0+%E6%9B%B8%E3%81%8D%E6%8F%9B%E3%81%88&oq=Javascript+%E8%A6%81%E7%B4%A0%E3%80%80&aqs=chrome.5.69i57j0l7.8194j0j4&sourceid=chrome&ie=UTF-8
1296 https://uxmilk.jp/30323
1295 https://www.google.com/search?q=javascript+list+%E9%95%B7%E3%81%95&oq=Javascript+list+naga&aqs=chrome.1.69i57j0.6458j0j4&sourceid=chrome&ie=UTF-8
1294 http://blog.pionet.co.jp/experience/archives/487
1293 https://www.google.com/search?sxsrf=ALeKk033aD7cSNlHkJFeXAwuZ90MCi4JlQ%3A1590983165003&ei=_HnUXrXaPLnWmAXfhYOoAg&q=javascript+function+%E6%8A%9C%E3%81%91%E3%82%8B&oq=Javascript+function+&gs_lcp=CgZwc3ktYWIQARgFMgIIADICCAAyAggAMgIIADICCAAyAggAMgIIADICCAA6BAgjECc6BAgAEAQ6BAgAEENQkypYq1NgqGRoAXAAeACAAVOIAbkJkgECMTaYAQCgAQGqAQdnd3Mtd2l6&sclient=psy-ab
1291 https://www.google.com/search?q=Javascript+break&oq=Javascript+break&aqs=chrome..69i57j0l7.4840j0j4&sourceid=chrome&ie=UTF-8
1292 https://devel

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


1276 https://sc.ha-sys.co.jp/files/Oracle_to_MySQL.pdf
1139 https://www.ispirer.jp/products/oracle-to-mariadb-migration
1274 https://mariadb.com/kb/en/what-should-i-know-if-i-am-moving-database-from-oracle-to-mariadb/
1185 https://mariadb.com/kb/en/moving-to-mariadb-moving-from-oracle-to-mariadb/
1186 https://mariadb.com/kb/en/mariadb-vs-oracle/
1273 https://mariadb.com/kb/en/connect/
1271 https://www.google.com/search?sxsrf=ALeKk00f5q2hmiNV-8wpo0mFDBa6K6be2w%3A1590653556577&ei=dHLPXvbrIpDc0gSu2bTQDQ&q=Oracle+MariaDB+windows&oq=Oracle+MariaDB+windows&gs_lcp=CgZwc3ktYWIQDDIECCMQJ1AAWABglooDaABwAHgAgAGDAYgBgwGSAQMwLjGYAQCqAQdnd3Mtd2l6&sclient=psy-ab&ved=0ahUKEwj29cyhjtbpAhUQrpQKHa4sDdoQ4dUDCAw
1272 https://qiita.com/jeyei/items/44ea0fc15622320a1130
1270 https://www.google.com/search?sxsrf=ALeKk02v4ey7e2_5hgu3dmhI55VwelVtsw%3A1590652318754&ei=nm3PXo7LLYKMr7wPu5mj8AQ&q=Oracle+MariaDB+windows&oq=Oracle+MariaDB+windows&gs_lcp=CgZwc3ktYWIQAzIFCAAQzQI6BAgAEEc6BwgjEOoCECc6BAgjECc6BggjECcQEzoECA

1229 https://www.google.com/search?sxsrf=ALeKk03W-cL4xmgvjzIP-0NJ1u3vX_2zGA%3A1590647732924&ei=tFvPXouCOKiNr7wPx8ag4Ag&q=Oracle+MariaDB+integration&oq=Oracle+MariaDB+integration&gs_lcp=CgZwc3ktYWIQAzIECCMQJzoGCCMQJxATOgIIADoECAAQHjoECAAQBDoGCAAQBBAeOggIABAIEAQQHjoFCAAQzQI6BggAEAgQHjoHCCMQsAIQJzoECCEQFVCX1QRYgKUFYPmoBWgIcAB4AIABaogB7A-SAQQyMy4xmAEAoAEBqgEHZ3dzLXdpeg&sclient=psy-ab&ved=0ahUKEwiLrNXI-NXpAhWoxosBHUcjCIwQ4dUDCAw&uact=5
1227 https://www.google.com/search?q=Oracle+MariaDB+%E7%A7%BB%E8%A1%8C%E6%89%8B%E9%A0%86&oq=Oracle%E3%80%80MariaDB%E3%80%80%E7%A7%BB%E8%A1%8C%E6%89%8B%E9%A0%86&aqs=chrome..69i57j0l2.17986j0j4&sourceid=chrome&ie=UTF-8
1228 https://qiita.com/rirne/items/d973b6678981e46326a4
1212 https://docs.aws.amazon.com/ja_jp/dms/latest/sbs/CHAP_RDSOracle2PostgreSQL.html
1215 https://docs.aws.amazon.com/ja_jp/dms/latest/sbs/CHAP_RDSOracle2PostgreSQL.Steps.InstallSCT.html
1226 https://sourceforge.net/projects/ora2pg/
1225 https://sourceforge.net/projects/ora2pg/postdownload
1

...

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


259 https://blog-imgs-52-origin.fc2.com/s/y/m/symfoware/488_01.png
257 https://jquery.com/download/#jquery
260 https://code.jquery.com/jquery-3.4.1.min.js
261 https://www.html5rocks.com/en/tutorials/developertools/sourcemaps/
258 https://code.jquery.com/jquery-3.4.1.slim.min.js
256 https://jquery.com/download/
254 https://symfoware.blog.fc2.com/blog-entry-1515.html
253 https://www.google.com/search?ei=eUmBXpmmF5Gl-Qa6gZ2gDQ&q=chrome+%E6%8B%A1%E5%BC%B5+html+%E6%9B%B8%E3%81%8D%E6%8F%9B%E3%81%88&oq=chrome+%E6%8B%A1%E5%BC%B5+ht&gs_lcp=CgZwc3ktYWIQARgBMgIIADICCAAyAggAMgIIADICCAAyAggAOgYIABAIEB46BAgAEEM6BAgAEARQoBFYkE1gkV5oBHAAeACAAU-IAb4EkgEBOJgBAKABAaoBB2d3cy13aXo&sclient=psy-ab
252 https://www.google.com/search?ei=dUiBXomqOJeGoATI5b2QDg&q=chrome+%E6%8B%A1%E5%BC%B5+%E8%A1%A8%E7%A4%BA&oq=Chrome+%E6%8B%A1%E5%BC%B5+h&gs_lcp=CgZwc3ktYWIQAxgFMgQIABAEMgQIABAEMgQIABAEMgQIABAEMgIIADIECAAQBDIECAAQBDIECAAQBDoOCAAQ6gIQtAIQmgEQ5QI6BwgAEIMBEAQ6BQgAEIMBOgQIABBDOgcIABCDARBDOgQIIRAVOgQIABAeOggIABAEEAoQHjo

108 https://448.jp/blog/article/1424/
105 https://www.google.com/search?q=%EF%BD%8B%E3%81%98%E3%82%87%EF%BD%8A%EF%BD%8B%EF%BD%90&oq=%EF%BD%8B%E3%81%98%E3%82%87%EF%BD%8A%EF%BD%8B%EF%BD%90&aqs=chrome..69i57.4927j0j4&sourceid=chrome&ie=UTF-8
101 https://github.com/gurutaka/extensions_hundsOn
102 https://github.com/gurutaka/extensions_hundsOn/tree/master/ex2
104 https://github.com/gurutaka/extensions_hundsOn/blob/master/ex2/manifest.json
103 https://github.com/gurutaka/extensions_hundsOn/blob/master/ex2/popup.js
100 https://www.nishishi.com/javascript-tips/element-bgcolor.html
99 https://www.google.com/search?ei=Cgp7Xoe-E4vg-AaqnYPoBA&q=javascript+%E8%83%8C%E6%99%AF%E8%89%B2+%E5%A4%89%E6%9B%B4&oq=Javascript%E3%80%80%E6%8B%9D%E5%95%93&gs_l=psy-ab.3.0.0i10i42j0i10l7.22932.32418..34522...8.0..0.99.2811.38......0....1..gws-wiz.....6..0j0i131j0i67j0i131i4j0i4j0i362i308i154i357j0i131i67.xsHQnWVB5GM
98 https://www.google.com/search?ei=0gl7XpCPH5n_wAPRz4nAAg&q=Chrome%E3%80%80%E6%8B%A1%E5%BC%B5%E3%

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


46 https://sourceforge.net/projects/sbcl/files/sbcl/1.2.7/sbcl-1.2.7-x86-64-windows-binary.msi/download
45 https://sourceforge.net/projects/sbcl/files/sbcl/1.2.7/
44 https://sourceforge.net/projects/sbcl/files/sbcl/
41 http://www.sbcl.org/platform-table.html
42 http://www.sbcl.org/news.html#2.0.2
40 http://www.sbcl.org/getting.html
39 https://www.google.com/search?ei=mnF4XqDzH4P4hwOEsIDICQ&q=SBCL+install&oq=SBCL+install&gs_l=psy-ab.3..0j0i30l7.3611.7628..7854...1.0..0.84.1095.15......0....1..gws-wiz.....6..0i67j0i362i308i154i357j0i4j0i131i4j0i131.ZLfupuHy1UQ&ved=0ahUKEwigqNCblbDoAhUD_GEKHQQYAJkQ4dUDCAs&uact=5
38 https://www.google.com/search?q=ex&oq=ex&aqs=chrome..69i57j0l7.1487j0j8&sourceid=chrome&ie=UTF-8
36 https://code.visualstudio.com/
35 https://www.google.com/search?ei=NWl4XoKfMZri-AaEuo6YCA&q=Visuaql+studio+code&oq=Visuaql+studio+code&gs_l=psy-ab.3..0i13l8.1393.1393..1921...0.0..0.76.210.3......0....1..gws-wiz.......0i7i10i30.tZWsPe88_GU&ved=0ahUKEwjCjYWbjbDoAhUaMd4KHQSdA4MQ4dU

## output text

In [8]:
with open('test.txt', mode='a', encoding='utf8') as f:
    for t in text:
        f.write(t)

In [12]:
all_lines = []
with open('test.txt', mode='r', encoding='utf8') as f:
    lines = f.readlines()
    for i in range(len(lines)):
        all_lines.append(lines[i])

In [111]:
try:
    url = "https://qiita.com/Hironsan/items/2466fe0f344115aff177"
    html = req.get(url).content
    soup = BeautifulSoup(html, 'html.parser')
    texts = soup.find_all('p')
    test = []
    for p in texts:
        test.append(p.get_text())
    print(test)
except:
    print(url, "NO")

['自然言語処理に前処理は不可欠です。テキストは文字の羅列であり構造化されていないため、そのままでは処理するのが難しいです。特にWebテキストの中には HTMLタグ や JavaScript のコードといったノイズが含まれています。このようなノイズは前処理して取り除かなければ期待する結果は得られないでしょう。', '\n出典: Deep learning for computational biology', '本記事では自然言語処理における前処理の種類とその威力について説明します。説明順序としては、はじめに前処理の種類を説明します。各前処理については、1.どんな処理なのか、2.なぜその処理をするのか、3.実装方法(なるべく) という観点から説明します。種類について説明した後、前処理の威力を測るために前処理をした場合としなかった場合での文書分類の結果を比較します。', 'この節では以下に示す5つの前処理について説明します。5つの前処理について、1.どんな処理なのか、2.なぜその処理をするのか、3.実装方法という観点から説明します。', '', 'テキストのクリーニングでは、テキスト内に含まれるノイズを除去します。よくあるノイズとして、JavaScriptのコードやHTMLタグが挙げられます。これらのノイズを除去することで、ノイズがタスクの結果に及ぼす悪影響を抑えることができます。以下のようなイメージです:\n', 'JavaScriptやHTMLタグの除去はよく行われるのですが、実際にはデータに応じて除去したいノイズは変わります。そのような場合に使える手として正規表現があります。正規表現を書く際には以下のようなオンラインエディタを使ってリアルタイムにパターンマッチを確認しながら行うと、作業が捗ります。', 'https://regex101.com/\n', 'Pythonには Beautiful Soup や lxml のようなクリーニングを行うのに便利なライブラリがあります。\nBeautifulSoupを用いたテキストのクリーニング例はこちら:\npreprocessings/ja/cleaning.py', '日本語のように単語の区切りが明らかでない言語に対してまず行われるのが単語の分割処理です。単語を分割する理由として、ほとんどの自然言語処理システムでは入

In [264]:
p1 = [[0, 1], [0, 2], [0, 3], [0, 4], [0, 5], [0, 6], [0, 7], [0, 8], [0, 9], [0, 10], [0, 11], [0, 12], [0, 13], [0, 14], [0, 15], [0, 16], [0, 17], [0, 18], [0, 19], [0, 20], [0, 21], [0, 22], [0, 23], [0, 24], [0, 25], [0, 26], [0, 27], [0, 28], [0, 29], [0, 30], [0, 31], [0, 32], [0, 33], [0, 34], [0, 35], [0, 36], [0, 37], [0, 38], [0, 39], [0, 40], [0, 41], [0, 42], [0, 43], [0, 44], [0, 45], [0, 46], [0, 47], [0, 48], [0, 49], [0, 50]]

In [265]:
p2 = [(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]

In [ ]:
[(0, 0.02), (1, 0.02)]

[[(0, 0.02), (1, 0.01)],
[0.01]]

In [279]:
for i in range(len(p2)):
    p1[p2[i][0]][0] += p2[i][1]            

[[0.04, 1],
 [0.04, 2],
 [0.04, 3],
 [0.04, 4],
 [0.04, 5],
 [0.04, 6],
 [0.04, 7],
 [0.04, 8],
 [0.04, 9],
 [0.04, 10],
 [0.04, 11],
 [0.04, 12],
 [0.04, 13],
 [0.04, 14],
 [0.04, 15],
 [0.04, 16],
 [0.04, 17],
 [0.04, 18],
 [0.04, 19],
 [0.04, 20],
 [0.04, 21],
 [0.04, 22],
 [0.04, 23],
 [0.04, 24],
 [0.04, 25],
 [0.04, 26],
 [0.04, 27],
 [0.04, 28],
 [0.04, 29],
 [0.04, 30],
 [0.04, 31],
 [0.04, 32],
 [0.04, 33],
 [0.04, 34],
 [0.04, 35],
 [0.04, 36],
 [0.04, 37],
 [0.04, 38],
 [0.04, 39],
 [0.04, 40],
 [0.04, 41],
 [0.04, 42],
 [0.04, 43],
 [0.04, 44],
 [0.04, 45],
 [0.04, 46],
 [0.04, 47],
 [0.04, 48],
 [0.04, 49],
 [0.04, 50]]

In [261]:
ls

[0.1, 0, 0, 0, 0, 0, 0, 0, 0, 0]

In [193]:
for i in range(len(ls)):
    for j in range(len(ls[i])):
        topic_num[ls[i][j][0]][0] += ls[i][j][1]
topic_num

[[13.680420979857445, 1],
 [0.8126377761363983, 2],
 [3.770515650510788, 3],
 [0.07999999821186066, 4],
 [6.344498805701733, 5],
 [0.07999999821186066, 6],
 [4.06588388979435, 7],
 [2.1705988943576813, 8],
 [0.07999999821186066, 9],
 [0.206787109375, 10],
 [33.49558566510677, 11],
 [2.107652187347412, 12],
 [0.30578888952732086, 13],
 [2.8755773156881332, 14],
 [0.8463706225156784, 15],
 [0.07999999821186066, 16],
 [0.38593749701976776, 17],
 [0.430059477686882, 18],
 [2.4432288259267807, 19],
 [6.166474133729935, 20],
 [5.647540092468262, 21],
 [16.70853890478611, 22],
 [3.7591269314289093, 23],
 [0.923238605260849, 24],
 [1.5139564275741577, 25],
 [0.07999999821186066, 26],
 [3.7254211232066154, 27],
 [0.07999999821186066, 28],
 [2.2449121475219727, 29],
 [11.265472516417503, 30],
 [0.3309515118598938, 31],
 [0.3641832023859024, 32],
 [1.0664669796824455, 33],
 [0.5351848155260086, 34],
 [1.1259266883134842, 35],
 [13.266709923744202, 36],
 [5.985078006982803, 37],
 [1.99234604090452

In [148]:
topic_num_sort = sorted(topic_num, reverse=True)
topic_num_sort

[[8.373896416276693, 11],
 [4.1771347261965275, 22],
 [3.420105244964361, 1],
 [3.3166774809360504, 36],
 [2.999446539208293, 39],
 [2.816368129104376, 30],
 [2.0768049973994493, 40],
 [1.6381251271814108, 44],
 [1.5927369631826878, 48],
 [1.5861247014254332, 5],
 [1.5416185334324837, 20],
 [1.4962695017457008, 37],
 [1.4444334916770458, 50],
 [1.4118850231170654, 21],
 [1.0164709724485874, 7],
 [0.942628912627697, 3],
 [0.9397817328572273, 23],
 [0.9313552808016539, 27],
 [0.7188943289220333, 14],
 [0.6108072064816952, 19],
 [0.5612280368804932, 29],
 [0.5426497235894203, 8],
 [0.526913046836853, 12],
 [0.4980865102261305, 38],
 [0.37848910689353943, 25],
 [0.33999742940068245, 42],
 [0.2881055027246475, 43],
 [0.28148167207837105, 35],
 [0.2666167449206114, 33],
 [0.23080965131521225, 24],
 [0.2115926556289196, 15],
 [0.20315944403409958, 2],
 [0.13379620388150215, 34],
 [0.1075148694217205, 18],
 [0.09648437425494194, 17],
 [0.0910458005964756, 32],
 [0.08273787796497345, 31],
 [0.0

In [162]:
topic_num_sort[:10]

[[8.373896416276693, 11],
 [4.1771347261965275, 22],
 [3.420105244964361, 1],
 [3.3166774809360504, 36],
 [2.999446539208293, 39],
 [2.816368129104376, 30],
 [2.0768049973994493, 40],
 [1.6381251271814108, 44],
 [1.5927369631826878, 48],
 [1.5861247014254332, 5]]

In [298]:
test2 = ['テスト',
        '彼はわがままだ',
        'いいえなんでもありません',
        'かくれんぼしよう']